In [ ]:
import numpy as np
import tensorflow as tf
from tensorflow import keras
from sklearn.datasets import make_classification
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
import random
import joblib

# Creating Reproducible Datasets

In [ ]:
# 1. Set random seeds for reproducibility
# Définir les graines aléatoires pour la reproductibilité
random.seed(42)           # Pour le module random
np.random.seed(42)        # Pour NumPy
tf.random.set_seed(42)    # Pour TensorFlow

print("✓ Graines aléatoires définies avec succès !")

In [ ]:
# 2. Generate synthetic data
# Générer des données synthétiques pour la classification
X, y = make_classification(
    n_samples=1000,        # 1000 exemples
    n_features=20,         # 20 caractéristiques
    n_informative=15,      # 15 caractéristiques utiles
    n_redundant=5,         # 5 caractéristiques redondantes
    n_classes=2,           # 2 classes (classification binaire)
    random_state=42        # Graine aléatoire pour reproductibilité
)

print(f"✓ Données générées : {X.shape[0]} exemples, {X.shape[1]} caractéristiques")

# Training Reproducible Model

In [ ]:
# 3. Split and scale the data
# Diviser les données en ensembles d'entraînement (80%) et de test (20%)
X_train, X_test, y_train, y_test = train_test_split(
    X, y, 
    test_size=0.2,         # 20% pour le test
    random_state=42        # Important pour la reproductibilité !
)

# Normaliser les données (StandardScaler centre les données autour de 0)
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)  # Apprendre et transformer les données d'entraînement
X_test = scaler.transform(X_test)        # Transformer les données de test

print(f"✓ Données divisées :")
print(f"  - Entraînement : {X_train.shape[0]} exemples")
print(f"  - Test : {X_test.shape[0]} exemples")

In [ ]:
# Sauvegarder les données d'entraînement et de test pour la reproductibilité
joblib.dump((X_train, y_train), 'train_data.pkl')
joblib.dump((X_test, y_test), 'test_data.pkl')

print("✓ Données sauvegardées :")
print("  - train_data.pkl")
print("  - test_data.pkl")

## Model Initalization and Training

In [ ]:
# 4. Build a neural network
model = keras.Sequential([
    keras.layers.Dense(32, activation='relu', input_shape=(X_train.shape[1],)),
    keras.layers.Dense(16, activation='relu'),
    keras.layers.Dense(1, activation='sigmoid')
])

model.compile(
    optimizer='adam',
    loss='binary_crossentropy',
    metrics=['accuracy']
)

In [ ]:
# 5. Train the model
model.fit(X_train, y_train, epochs=20, batch_size=32, validation_split=0.1)

In [ ]:
# 6. Evaluate the model
loss, accuracy = model.evaluate(X_test, y_test)
print(f"Test accuracy: {accuracy:.2f}")

# Saving Models

In [ ]:
# 7. Save the model and scaler
# Sauvegarder le modèle entraîné
model.save('my_model.keras')

print("✓ Modèle sauvegardé : my_model.keras")

# Reproducing Models

In [ ]:
#8. Reloading model later
# Recharger le modèle et les données sauvegardées
from tensorflow.keras.models import load_model

modelReloaded = load_model('my_model.keras')
X_train_reloaded, y_train_reloaded = joblib.load('train_data.pkl')
X_test_reloaded, y_test_reloaded = joblib.load('test_data.pkl')

print("✓ Modèle et données rechargés avec succès !")

In [ ]:
# Vérifier que le modèle rechargé donne les mêmes résultats
loss_reloaded, accuracy_reloaded = modelReloaded.evaluate(X_test_reloaded, y_test_reloaded)
print(f"\n🎯 Précision du modèle rechargé : {accuracy_reloaded:.2f}")
print("\n💡 Si la précision est identique à celle obtenue plus haut,")
print("   votre workflow est reproductible ! ✓")